In [1]:
# 라이브러리 설치
import pandas as pd
import numpy as np
from pprint import pprint
import pickle
from tqdm import tqdm_notebook
from time import time
import os

from gensim import corpora
from gensim.models import AuthorTopicModel
from gensim.models import CoherenceModel
from gensim.corpora import Dictionary, bleicorpus # bleicorpus는 저장을 하기 위한 용도일 뿐임

# 사용자간의 유사성을 평가하기 위한 measure를 사용하기 위해 불러오기
# 어떤 두 개의 확률분포의 차이를 보겠다
from gensim.matutils import hellinger
from gensim import matutils

import matplotlib.pyplot as plt

# 1. 데이터 불러오기

In [2]:
path_df_final = r"C:\Users\user\Desktop\새 폴더\data\빅카인즈_통합_final.xlsx"

In [3]:
data = pd.read_excel(path_df_final, index_col=False)
data.reset_index(drop=True, inplace=True)


In [4]:
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 법원 과도 님비 현상 제동 향후 님비 현상 균열...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 청년 공간 다양 창업 기회 제공 시작 도움 두리하나...  
3     아시안 게임 메달 선수 세상 즐거움 인내 장애 불편 불행 장애인 체육회 탁구 선수 ...  
4     청소년 미래 재단 상담 안전 구축 자기 개발 기회 제공 종합 지원 거점 공연장 상담...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4533  청년 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업인 ...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 기원 발전 성원 지지 시민 소임 공직자...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4537 entries, 0 to 4536
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Author           4537 non-null   object
 1   Title            4537 non-null   object
 2   Content          4537 non-null   object
 3   Extracted_Nouns  4537 non-null   object
dtypes: object(4)
memory usage: 141.9+ KB


In [6]:
# 결측값이 있는 행 제거
data = data.dropna(axis=0)
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 법원 과도 님비 현상 제동 향후 님비 현상 균열...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 청년 공간 다양 창업 기회 제공 시작 도움 두리하나...  
3     아시안 게임 메달 선수 세상 즐거움 인내 장애 불편 불행 장애인 체육회 탁구 선수 ...  
4     청소년 미래 재단 상담 안전 구축 자기 개발 기회 제공 종합 지원 거점 공연장 상담...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4533  청년 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업인 ...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 기원 발전 성원 지지 시민 소임 공직자...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

In [7]:
data.reset_index(drop=True, inplace=True)
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 법원 과도 님비 현상 제동 향후 님비 현상 균열...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 청년 공간 다양 창업 기회 제공 시작 도움 두리하나...  
3     아시안 게임 메달 선수 세상 즐거움 인내 장애 불편 불행 장애인 체육회 탁구 선수 ...  
4     청소년 미래 재단 상담 안전 구축 자기 개발 기회 제공 종합 지원 거점 공연장 상담...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4533  청년 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업인 ...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 기원 발전 성원 지지 시민 소임 공직자...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

## 1-1. 전처리 완료된 데이터 가져오기

In [8]:
data['Extracted_Nouns']

0       극단 지역 이기주의 지역 현안 발목 법원 과도 님비 현상 제동 향후 님비 현상 균열...
1       취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...
2       두리하나 플라워 아이 결심 지방 청년 공간 다양 창업 기회 제공 시작 도움 두리하나...
3       아시안 게임 메달 선수 세상 즐거움 인내 장애 불편 불행 장애인 체육회 탁구 선수 ...
4       청소년 미래 재단 상담 안전 구축 자기 개발 기회 제공 종합 지원 거점 공연장 상담...
                              ...                        
4532    청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...
4533    청년 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업인 ...
4534    청년 농부 미래 딸기 학교 교육 지난달 천사 딸기 영농 조합 법인 출범 왼쪽 대표 ...
4535    시장 존경 시민 동료 공직자 새해 소원 성취 기원 발전 성원 지지 시민 소임 공직자...
4536    국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...
Name: Extracted_Nouns, Length: 4537, dtype: object

In [9]:
tokenized_data=[]
for i in range(len(data)):
    row = list(data.loc[i]['Extracted_Nouns'].split(" "))
    tokenized_data.append(row)

## 1-2. Author 설정

In [10]:
author = set(data["Author"])
len(author)

3

In [11]:
# author 별 나누기(index 추출)
authors = data.groupby('Author')

In [12]:
authors.groups

{'목포': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, ...], '무안': [1679, 1680, 1681, 1682, 1683, 1684, 1685, 1686, 1687, 1688, 1689, 1690, 1691, 1692, 1693, 1694, 1695, 1696, 1697, 1698, 1699, 1700, 1701, 1702, 1703, 1704, 1705, 1706, 1707, 1708, 1709, 1710, 1711, 1712, 1713, 1714, 1715, 1716, 1717, 1718, 1719, 1720, 1721, 1722, 1723, 1724, 1725, 1726, 1727, 1728, 1729, 1730, 1731, 1732, 1733, 1734, 1735, 1736, 1737, 1738, 1739, 1740, 1741, 1742, 1743, 1744, 1745, 1746, 1747, 1748, 1749, 1750, 1751, 1752, 1753, 1754, 1755, 1756, 1757, 1758, 1759, 1760, 1761, 1762, 1763, 1764, 1765, 1766, 1767, 1768, 1769, 1770, 1771, 1772, 1773, 1774, 1775, 1776, 1

In [13]:
type(authors.groups)

pandas.io.formats.printing.PrettyDict

In [14]:
# index로 각 지역별 뉴스기사
author2doc = {}
for user, index in authors.groups.items():
    author2doc[user] = list(index)

# 2. Author Topic Modeling

In [15]:
# ATM에 사용할 Dictionary 만들기
if not os.path.exists('./ATM_coh/ATM_dict'):
    dictionary = corpora.Dictionary(tokenized_data)
    dictionary.save('./ATM_coh/ATM_dict')
    print(dictionary)
else:
    dictionary = Dictionary.load('./ATM_coh/ATM_dict')



Dictionary<18945 unique tokens: ['갈등', '건물', '건축', '검토', '경종']...>


In [16]:
# ATM에 사용할 corpus 만들기
if not os.path.exists('./ATM_coh/ATM_corpus'):
    corpus = [dictionary.doc2bow(doc) for doc in tokenized_data]
    # BleiCorpus : pickle로 저장하는 것과 같다고 생각
    corpora.BleiCorpus.serialize('./ATM_coh/ATM_corpus', corpus)
else:
    corpus = bleicorpus.BleiCorpus('./ATM_coh/ATM_corpus')

In [17]:
# ATM에 들어갈 데이터 확인하기
print('Number of author: %d' % len(authors))
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of author: 3
Number of unique tokens: 18945
Number of documents: 4537


In [18]:
# dictionary함수로 만든 사전에 있는 단어 보기
for idx in dictionary:
    print(dictionary[idx])

갈등
건물
건축
검토
경종
과도
관계
관련
교육
균열
극단
근접
기관
기대
기피
기회
녹지
님비
묘지
문제
밀집
발목
발휘
법령
법원
변경
부당
부족
불허
비용
사실
사유
사회
상대
생활
소송
숙박
승소
시설
시장
신청
악영향
여건
역량
용도
운영
원고
의견
이기주의
이용
이유
일견
자연
자체
재판부
정서
정주
정치
정치력
정치인
제기
제동
조정
주거
주목
주민
주장
지역
처분
취소
취지
침해
판결
판시
편승
학생
학습
한탕주의
해당
행동
행정부
향후
허가
현상
현안
혐오
호불호
환경
감소
감소세
계획
고려
공동
배치
부과
부담금
상당
수가
신설
용지
인구
인정
조합
주변
주택
증축
초등학생
취학
필요
학교
행정
가게
가족
강사
강조
개발
개별
결심
결혼
경단녀
경력
경험
고객
고향
공간
관계자
관리
관심
구상
궁리
귀향
극복
근무
금액
기존
낭만
냉정
다양
단절
단점
대기
대부분
대상
대출
대학
도움
두리하나
디자인
마감
마련
마음
매장
메시지
멘토링
모델
모습
무늬
미소
반면
발판
방법
병원
보금자리
보람
본인
부지기수
부착
분야
분주
비결
비교
뿌리
사람
사례
사업
사이
사진
살이
상경
상품
생각
선순환
선입견
선정
선택
선택지
설립
성공
소멸
손님
수준
스마트
스토어
시간
시작
신약
아이
아이디어
안내
안정
안주
어린이집
여성
연구원
영상
요즘
위기
위치
유지
육아
의미
인건비
인식
일자리
입소
자리
자본
자신
장식
장점
전공
전문
전셋집
젊은이
정답
정도
정보
정부
정착
제공
제품
졸업
종잣돈
주도
주위
준비
지방
지원
지원금
지원책
지자체
직원
직장인
차별
참여
창업
창업자
창출
채용
처음
청년
초기
최고
최근
축제
카드
코드
퇴근
퇴사
특별
특성
평가
평소
포토
플라워
플로리스트
피부
하루하루
학원
한때
한약
한의원
행사장
행안부
혁신
화분
활기
효과
휴대폰
희망자
강자
개인전
게임
경쟁
계기
관왕
구슬땀
국가
국제
금메달
금빛
기억
농촌
단식
단체전
당시
대전
대표
대회
동네
동메달
동호인
등급
라켓
리그
마비
마을
메달
발탁
발현
보훈
복식
본

In [19]:
# 사람이 이해할 수 있는 형태로 코퍼스 사전 재구성 해보기 (term-frequency)
[[(dictionary[id], freq) for id, freq in cp] for cp in corpus]

[[('갈등', 1),
  ('건물', 2),
  ('건축', 2),
  ('검토', 1),
  ('경종', 1),
  ('과도', 2),
  ('관계', 2),
  ('관련', 1),
  ('교육', 1),
  ('균열', 1),
  ('극단', 1),
  ('근접', 1),
  ('기관', 1),
  ('기대', 1),
  ('기피', 3),
  ('기회', 1),
  ('녹지', 2),
  ('님비', 3),
  ('묘지', 1),
  ('문제', 3),
  ('밀집', 1),
  ('발목', 1),
  ('발휘', 1),
  ('법령', 1),
  ('법원', 2),
  ('변경', 4),
  ('부당', 1),
  ('부족', 1),
  ('불허', 3),
  ('비용', 1),
  ('사실', 1),
  ('사유', 2),
  ('사회', 2),
  ('상대', 1),
  ('생활', 1),
  ('소송', 1),
  ('숙박', 1),
  ('승소', 1),
  ('시설', 6),
  ('시장', 1),
  ('신청', 1),
  ('악영향', 1),
  ('여건', 1),
  ('역량', 1),
  ('용도', 4),
  ('운영', 1),
  ('원고', 1),
  ('의견', 1),
  ('이기주의', 1),
  ('이용', 1),
  ('이유', 2),
  ('일견', 1),
  ('자연', 3),
  ('자체', 1),
  ('재판부', 1),
  ('정서', 4),
  ('정주', 1),
  ('정치', 1),
  ('정치력', 1),
  ('정치인', 3),
  ('제기', 1),
  ('제동', 2),
  ('조정', 1),
  ('주거', 2),
  ('주목', 1),
  ('주민', 2),
  ('주장', 1),
  ('지역', 8),
  ('처분', 2),
  ('취소', 1),
  ('취지', 1),
  ('침해', 1),
  ('판결', 2),
  ('판시', 1),
  ('편승', 1),
  ('학생', 1),
  ('학습

In [20]:
corpus = list(corpus)

# ATM 모델 만들기

In [21]:
# Author Topic Model 실행 : 있으면 load하고 없으면 model을 만들기
if not os.path.exists("./ATM_coh/ATM_model"):
    model = AuthorTopicModel(corpus=corpus, num_topics=7, id2word=dictionary.id2token, author2doc=author2doc, passes=5000,)
    
    model.save('./ATM_coh/ATM_model')
else:
    model = AuthorTopicModel.load("./ATM_coh/ATM_model")

## 2-1. ATM 토픽 결과

In [22]:
# 토픽 라벨 지정. 
topic_labels = ["Topic0",
                "Topic1",
                "Topic2",
                "Topic3",
                "Topic4",
                "Topic5",
                "Topic6"]

In [23]:
# 토픽별로 topN 단어 확인하기.
for topic in model.show_topics(model.num_topics):
    print('Label: ' + topic_labels[topic[0]])
    words = ''
    for word, prob in model.show_topic(topic[0], topn=10):
        words += word + ' '
    print('Words: ' + words)
    print()

Label: Topic0
Words: 엽무 라이크 단물 산증인 함유량 켈리그라피 프리미어리그 세이브더칠드런 준거 신봉 

Label: Topic1
Words: 지역 교육 사업 지원 문화 추진 운영 계획 학교 청년 

Label: Topic2
Words: 세계 갯벌 마을 주민 지역 에너지 풍력 관광 해상 유산 

Label: Topic3
Words: 해변 영화 생쥐 탈수 승마 세수 블루플래그 위기관리 탈환 초가지붕 

Label: Topic4
Words: 엽무 라이크 단물 산증인 함유량 켈리그라피 프리미어리그 세이브더칠드런 준거 신봉 

Label: Topic5
Words: 노예 로타리 기착지 공과대 직파 대장암 숙성 석간 용도 변호 

Label: Topic6
Words: 치유 그림 명상 스파 한방 웰니스 뷰티 은행장 테라피 작전 



In [24]:
model.get_topic_terms(0)

[(15583, 5.278437894930791e-05),
 (15575, 5.278437866807346e-05),
 (15574, 5.278437866807346e-05),
 (15582, 5.2784378168254776e-05),
 (15555, 5.27843780139196e-05),
 (13001, 5.2784377929050266e-05),
 (13742, 5.27843778907008e-05),
 (13760, 5.278437787198506e-05),
 (13768, 5.278437787198506e-05),
 (13761, 5.278437787198506e-05)]

In [25]:
all_corpus_ids = []
for i in range(len(model.get_topics())):
    corpus_ids = [term_id for term_id, _ in model.get_topic_terms(i, topn=10)]
    all_corpus_ids.append(corpus_ids)

In [26]:
all_corpus_ids

[[15583, 15575, 15574, 15582, 15555, 13001, 13742, 13760, 13768, 13761],
 [67, 8, 174, 237, 397, 476, 45, 90, 109, 250],
 [320, 2073, 306, 65, 67, 955, 987, 914, 990, 2107],
 [1705, 1606, 18139, 18141, 2131, 12889, 15978, 16314, 16174, 17940],
 [15583, 15575, 15574, 15582, 15555, 13001, 13742, 13760, 13768, 13761],
 [15967, 18929, 12082, 14745, 15499, 14505, 14265, 14699, 44, 17866],
 [1145, 1295, 4010, 16355, 2066, 7635, 5202, 8358, 13283, 5799]]

#빈도

In [27]:
# 비교
# corpus
# [[(dictionary[id], freq) for id, freq in cp] for cp in corpus]


In [28]:
# import numpy as np

# corpus = [
#     [(0, 1), (1, 2), (2, 2), (3, 1), (4, 1), (5, 2), (6, 2), (7, 1), (8, 1), (9, 1)],
#     [(1, 1), (3, 1), (5, 1), (9, 1), (14, 3), (15, 1), (16, 2), (17, 3)],
#     [(0, 1), (1, 2), (2, 2), (3, 1), (4, 1), (5, 2), (6, 2), (7, 1), (8, 1), (9, 1)]
# ]

# all_corpus_ids = [
#     [1, 2, 3, 4, 5],
#     [6, 7],
#     [8, 9],
#     [10, 11],
#     [12],
#     [13],
#     [14],
#     [15],
#     [16],
#     [17]
# ]

def normalize_topic_distribution(doc_a, topic_ids):
    total_freq = sum(freq for _, freq in doc_a)
    topic_distribution = [0] * len(topic_ids)

    # 분모가 0인 경우 처리하여 정규화 수행
    if total_freq != 0:
        for topic_id in topic_ids:
            # topic_id가 doc_a에 포함되어 있는지 확인
            topic_freq = sum(freq for (corpus_id, freq) in doc_a if corpus_id in topic_id)
            topic_index = topic_ids.index(topic_id)
            topic_distribution[topic_index] = topic_freq / total_freq

    # 정규화된 토픽 분포의 합이 1이 되도록 조절
    sum_normalized_distribution = sum(topic_distribution)
    if sum_normalized_distribution != 0:
        topic_distribution = [value / sum_normalized_distribution for value in topic_distribution]

    return topic_distribution

# 각 문서별 정규화된 토픽 분포를 저장할 리스트
document_distributions = []

# 각 문서에 대해 토픽의 분포를 정규화하여 리스트에 추가
for doc_a in corpus:
    normalized_distribution = normalize_topic_distribution(doc_a, all_corpus_ids)
    document_distributions.append(normalized_distribution)

# 결과 출력
for i, distribution in enumerate(document_distributions, 1):
    print(f"Document {i}의 정규화된 토픽 분포: {distribution}")

Document 1의 정규화된 토픽 분포: [0.0, 0.4166666666666667, 0.4166666666666667, 0.0, 0.0, 0.16666666666666669, 0.0]
Document 2의 정규화된 토픽 분포: [0.0, 0.8571428571428571, 0.14285714285714285, 0.0, 0.0, 0.0, 0.0]
Document 3의 정규화된 토픽 분포: [0.0, 0.8571428571428572, 0.14285714285714285, 0.0, 0.0, 0.0, 0.0]
Document 4의 정규화된 토픽 분포: [0.0, 0.5, 0.5, 0.0, 0.0, 0.0, 0.0]
Document 5의 정규화된 토픽 분포: [0.0, 0.9285714285714286, 0.07142857142857142, 0.0, 0.0, 0.0, 0.0]
Document 6의 정규화된 토픽 분포: [0.0, 0.7999999999999999, 0.19999999999999998, 0.0, 0.0, 0.0, 0.0]
Document 7의 정규화된 토픽 분포: [0.0, 0.7499999999999999, 0.25, 0.0, 0.0, 0.0, 0.0]
Document 8의 정규화된 토픽 분포: [0.0, 0.5, 0.5, 0.0, 0.0, 0.0, 0.0]
Document 9의 정규화된 토픽 분포: [0.0, 0.9166666666666666, 0.08333333333333333, 0.0, 0.0, 0.0, 0.0]
Document 10의 정규화된 토픽 분포: [0.0, 0.7272727272727273, 0.2727272727272727, 0.0, 0.0, 0.0, 0.0]
Document 11의 정규화된 토픽 분포: [0.0, 0.8461538461538461, 0.15384615384615385, 0.0, 0.0, 0.0, 0.0]
Document 12의 정규화된 토픽 분포: [0.0, 0.9347826086956522, 0.0652173

In [29]:
len(document_distributions)

4537

In [30]:
a = pd.DataFrame(document_distributions)

In [31]:
a

0         1         2       3    4         5    6
0     0.0  0.416667  0.416667  0.0000  0.0  0.166667  0.0
1     0.0  0.857143  0.142857  0.0000  0.0  0.000000  0.0
2     0.0  0.857143  0.142857  0.0000  0.0  0.000000  0.0
3     0.0  0.500000  0.500000  0.0000  0.0  0.000000  0.0
4     0.0  0.928571  0.071429  0.0000  0.0  0.000000  0.0
...   ...       ...       ...     ...  ...       ...  ...
4532  0.0  1.000000  0.000000  0.0000  0.0  0.000000  0.0
4533  0.0  1.000000  0.000000  0.0000  0.0  0.000000  0.0
4534  0.0  1.000000  0.000000  0.0000  0.0  0.000000  0.0
4535  0.0  0.575000  0.412500  0.0125  0.0  0.000000  0.0
4536  0.0  0.302326  0.209302  0.0000  0.0  0.488372  0.0

[4537 rows x 7 columns]

In [32]:
topic_freq = pd.concat([data[["Author","Title","Content"]],a],axis=1) 

In [33]:
topic_freq.to_excel( r"C:\Users\user\Desktop\새 폴더\data\빅카인즈_통합_topic_freq.xlsx")

## 2-2. 지역과 토픽

In [34]:
for author, doc_ids in model.author2doc.items():
    print(f"\nAuthor: {author}")
    
    for topic_id, prob in model.get_author_topics(author):
        print(f"  Topic {topic_id}: {prob}")
    
    # 가장 높은 확률을 갖는 토픽 찾기
    max_prob_topic = max(model.get_author_topics(author), key=lambda x: x[1])
    max_prob_topic_id, max_prob = max_prob_topic
    
    print(f"  Best represented by Topic {max_prob_topic_id} with Probability {max_prob}")


Author: 목포
  Topic 1: 0.9999978576116092
  Best represented by Topic 1 with Probability 0.9999978576116092

Author: 무안
  Topic 1: 0.9749564218313902
  Topic 2: 0.012996050780910439
  Topic 5: 0.011009317311332869
  Best represented by Topic 1 with Probability 0.9749564218313902

Author: 신안
  Topic 1: 0.8183514938410148
  Topic 2: 0.15931085273023998
  Topic 5: 0.01056365714954173
  Best represented by Topic 1 with Probability 0.8183514938410148


In [ ]:
# 사용자별로 토픽 분포 확인하기.
# def show_author(name):
#     print('\n%s' % name) # 지역명
#     print('\nDocs:', model.author2doc[name])
#     print('\nTopics:')
#     pprint([(topic_labels[topic[0]], topic[1]) for topic in model[name]])

In [32]:
# model.get_author_topics("무안")
# model["무안"]
# show_author('무안')

# 종합해서 보기
# [model.get_author_topics(author) for author in model.id2author.values()]

In [201]:
# 모델 성능 확인

In [202]:
from gensim.models import atmodel
doc2author = atmodel.construct_doc2author(model.corpus, model.author2doc)

In [203]:
# Compute the per-word bound.
# Number of words in corpus.
corpus_words = sum(cnt for document in model.corpus for _, cnt in document)

# Compute bound and divide by number of words.
perwordbound = model.bound(model.corpus, author2doc=model.author2doc, \
                           doc2author=model.doc2author) / corpus_words
print(perwordbound)

-7.878874260040996


In [204]:
top_topics = model.top_topics(model.corpus)

In [205]:
top_topics

[([(0.013064192280044658, '지역'),
   (0.010901914042561049, '교육'),
   (0.010275873228613161, '사업'),
   (0.008524836558097102, '지원'),
   (0.006834326192937632, '문화'),
   (0.005244448602549456, '관광'),
   (0.005180330365409627, '추진'),
   (0.0045052717005253625, '운영'),
   (0.0041816120509059985, '사회'),
   (0.004126492632905288, '학교'),
   (0.004095133314769536, '도시'),
   (0.004037267890605726, '의원'),
   (0.004028924235896289, '계획'),
   (0.0039923929197844665, '환경'),
   (0.003977208255541137, '센터'),
   (0.003974818611625323, '산업'),
   (0.003782362711523825, '청년'),
   (0.0037166947427858315, '전국'),
   (0.003691497967546369, '해양'),
   (0.0036904657253657865, '시설')],
  -1.2299614945830377),
 ([(0.018237478599834846, '지역'),
   (0.01175113479677234, '갯벌'),
   (0.01064789668604014, '사업'),
   (0.010468979589552629, '교육'),
   (0.009200764654792668, '주민'),
   (0.008870386954261263, '지원'),
   (0.0066641649717547515, '세계'),
   (0.00625774440125325, '마을'),
   (0.005718026979357133, '인구'),
   (0.005531152

# 시각화_지역별

In [206]:
from sklearn.manifold import TSNE
tsne = TSNE(n_components=2, perplexity=2, random_state=0)
authors = range(3)
_ = tsne.fit_transform(model.state.gamma[authors, :])

In [207]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

In [208]:
from bokeh.models import HoverTool
from bokeh.plotting import figure, show, ColumnDataSource

In [209]:
x = tsne.embedding_[:, 0]
y = tsne.embedding_[:, 1]
author_names = [model.id2author[a] for a in authors]
author_sizes = [len(model.author2doc[a]) for a in author_names]

In [210]:
scale = 0.1
author_sizes = [len(model.author2doc[a]) for a in author_names]
radii = [size * scale for size in author_sizes]

In [211]:
source = ColumnDataSource(
        data=dict(
            x=x,
            y=y,
            author_names=author_names,
            author_sizes=author_sizes,
            radii=radii,
        )
    )


hover = HoverTool(
        tooltips=[
        ("author", "@author_names"),
        ("size", "@author_sizes"),
        ]
    )

p = figure(tools=[hover, 'crosshair,pan,wheel_zoom,box_zoom,reset,save,lasso_select'])
p.scatter('x', 'y', radius='radii', source=source, fill_alpha=0.6, line_color=None)
show(p)

In [212]:
all_list = list(model.id2author.values())
tmp_l = []
for a in all_list:
    for topic in model[a]:
        tmp_l.append([topic[0], a, topic[1]])

In [213]:
tmp_df = pd.DataFrame(tmp_l)
tmp_df.columns = ['topic_id','author', 'prob']

In [214]:
tmp_df

topic_id author      prob
0         0     목포  0.997370
1         0     무안  0.743804
2         4     무안  0.256167
3         0     신안  0.690721
4         1     신안  0.015139
5         4     신안  0.293446

In [215]:
tmp_df.sort_values(['topic_id', 'prob'], inplace=True)

In [216]:
tmp_df_rank = tmp_df.groupby(['topic_id'])

In [217]:
tmp_df_rank.head(3)

topic_id author      prob
3         0     신안  0.690721
1         0     무안  0.743804
0         0     목포  0.997370
4         1     신안  0.015139
2         4     무안  0.256167
5         4     신안  0.293446

# 일단 보류

In [ ]:
# tmp_df = pd.DataFrame(tmp_l)
# tmp_df.columns = ['author', 'topic_id', 'prob']
# tmp_df = tmp_df[['topic_id','author', 'prob']]
# tmp_df.sort_values(['topic_id', 'prob'], inplace=True)
# tmp_df.reset_index(drop=True, inplace=True)
# tmp_df_rank = tmp_df.groupby(['topic_id']).tail(3)
# tmp_df_rank['rank'] = model.num_topics * [3 - i for i in range(3)]
# tmp_df_rank.sort_values(['topic_id', 'rank'], inplace=True)
# tmp_df_rank

In [ ]:
# 토픽별 하위 10개 판매처
a_list = list(model.id2author.values())
tmp_l = []
for a in a_list:
    for topic in model[a]:
        tmp_l.append([a, topic[0], topic[1]])


tmp_df = pd.DataFrame(tmp_l)
tmp_df.columns = ['author', 'topic_id', 'prob']
tmp_df = tmp_df[['topic_id','author', 'prob']]
tmp_df.sort_values(['topic_id', 'prob'], inplace=True, ascending=False)
tmp_df.reset_index(drop=True, inplace=True)
tmp_df_top10 = tmp_df.groupby(['topic_id']).tail(3)
tmp_df_top10['rank'] = model.num_topics * [3 - i for i in range(3)]
tmp_df_top10.sort_values(['topic_id', 'rank'], inplace=True)
tmp_df_top10

In [121]:
# author-topic 분포 만들기
#author_vecs = [model[author] for author in model.id2author.values()]
author_vecs = [model.get_author_topics(market) for market in model.id2author.values()]
 
def similarity(vec1, vec2):
    # vec1, vec2 사이의 hellinger similarity 구하기.
    dist = hellinger(matutils.sparse2full(vec1, model.num_topics), \
                              matutils.sparse2full(vec2, model.num_topics))
    sim = 1.0 / (1.0 + dist)
    return sim
 
def get_sims(vec):
    # 각 사용자들 사이의 similarity pair 구하기.
    sims = [similarity(vec, vec2) for vec2 in author_vecs]
    return sims
 
def get_table(name, top_n=10, smallest_author=1): # top_n은 나랑 비슷한 저자 수
    """
    주어진 사용자에 대해서 topN 사람만큼 유사도를 정렬해서 table을 출력하는 함수입니다.
    """
    
    # 유사도 측정하기
    sims = get_sims(model.get_author_topics(name))
 
    # 저자별 정보 정렬하기
    table = []
    for elem in enumerate(sims):
        author_name = model.id2author[elem[0]]
        sim = elem[1]
        # 저자가 몇 개의 문서에 등장했는지를 알 수 있음
        author_size = len(model.author2doc[author_name])
        if author_size >= smallest_author:
            table.append((author_name, sim, author_size)) # table에 유저에 대한 정보를 넣어줌
            
    # 사용자 패턴 분석 결과를 Dataframe으로 만들기
    df = pd.DataFrame(table, columns=['Author', 'Score', 'Size'])
    df = df.sort_values('Score', ascending=False)[:top_n] # ascending을 False로 해줘야함(유사성을 찾기 위함)
    
    return df

In [122]:
# 지역별 패턴 검증 : 유사한 지역 확인
get_table('무안')

Author     Score  Size
1     무안  1.000000  1238
0     목포  0.976958  1679
2     신안  0.900577  1620